In [1]:
from __future__ import absolute_import
from __future__ import division
from __future__ import print_function

#Imports
import os
import numpy as np
import tensorflow as tf
import cv2
from sklearn.utils import shuffle

In [2]:
#data directory

img_dir="../gen_script/data_sample"
img_dir_same = img_dir + "/1"
img_dir_diff = img_dir + "/0"

In [ ]:
X = np.array([[1., 0.], [2., 1.], [0., 0.]])
y = np.array([0, 1, 2])


X, y

In [3]:
def load_data(img_dir, label):
        list_of_imgs = []
        list_of_labels = []
        for img in os.listdir(img_dir):
                img = os.path.join(img_dir, img)
#                 print(img)
                if not img.endswith(".png"):
                        continue
                a = cv2.imread(img)
                
                if a is None:
                        print ("Unable to read image{}".format(img))
                        continue
                flattened_a = a.flatten()
#                 flattened_a = tf.cast(flattened_a, tf.float32)
                
                list_of_imgs.append(np.asarray(flattened_a, dtype=np.float32))
#                 list_of_imgs.append(a)
                list_of_labels.append(label)
        data_labels = np.asarray(list_of_labels, dtype=np.int32)
        data_imgs = np.array(list_of_imgs)
#         data_labels = np.array(list_of_labels)
        return data_imgs, data_labels

In [4]:
tf.logging.set_verbosity(tf.logging.INFO)
    
def cnn_model_fn(features, labels, mode):
  """Model function for CNN."""
  # Input Layer
  # Reshape X to 4-D tensor: [batch_size, width, height, channels]
  # MNIST images are 28x28 pixels, and have one color channel
  input_layer = tf.reshape(features["x"], [-1, 60, 60, 3])

  # Convolutional Layer #1
  # Computes 32 features using a 5x5 filter with ReLU activation.
  # Padding is added to preserve width and height.
  # Input Tensor Shape: [batch_size, 28, 28, 1]
  # Output Tensor Shape: [batch_size, 28, 28, 16]
  conv1 = tf.layers.conv2d(
      inputs=input_layer,
      filters=16,
      kernel_size=[4, 4],
      padding="same",
      activation=tf.nn.relu)

  # Pooling Layer #1
  # First max pooling layer with a 2x2 filter and stride of 2
  # Input Tensor Shape: [batch_size, 60, 60, 16]
  # Output Tensor Shape: [batch_size, 20, 20, 16]
  pool1 = tf.layers.max_pooling2d(inputs=conv1, pool_size=[3, 3], strides=2)

  # Convolutional Layer #2
  # Computes 64 features using a 5x5 filter.
  # Padding is added to preserve width and height.
  # Input Tensor Shape: [batch_size, 20, 20, 16]
  # Output Tensor Shape: [batch_size, 20, 20, 32]
  conv2 = tf.layers.conv2d(
      inputs=pool1,
      filters=32,
      kernel_size=[2, 2],
      padding="same",
      activation=tf.nn.relu)

  # Pooling Layer #2
  # Second max pooling layer with a 2x2 filter and stride of 2
  # Input Tensor Shape: [batch_size, 14, 14, 64]
  # Output Tensor Shape: [batch_size, 7, 7, 64]
  pool2 = tf.layers.max_pooling2d(inputs=conv2, pool_size=[3, 3], strides=2)

  # Flatten tensor into a batch of vectors
  # Input Tensor Shape: [batch_size, 7, 7, 64]
  # Output Tensor Shape: [batch_size, 7 * 7 * 64]
#   pool2_flat = tf.reshape(pool2, [-1, 14 * 14 * 32])


  conv3 = tf.layers.conv2d(
      inputs=pool2,
      filters=64,
      kernel_size=[4, 4],
      padding="same",
      activation=tf.nn.relu)

  # Pooling Layer #2
  # Second max pooling layer with a 2x2 filter and stride of 2
  # Input Tensor Shape: [batch_size, 14, 14, 64]
  # Output Tensor Shape: [batch_size, 7, 7, 64]
  pool3 = tf.layers.max_pooling2d(inputs=conv3, pool_size=[2, 2], strides=2)
  print("pool3.shape******")
  print(pool3.shape)

  # Flatten tensor into a batch of vectors
  # Input Tensor Shape: [batch_size, 7, 7, 64]
  # Output Tensor Shape: [batch_size, 7 * 7 * 64]
  pool3_flat = tf.reshape(pool3, [-1, 7 * 7 * 64])

  # Dense Layer
  # Densely connected layer with 1024 neurons
  # Input Tensor Shape: [batch_size, 7 * 7 * 64]
  # Output Tensor Shape: [batch_size, 1024]
  dense = tf.layers.dense(inputs=pool3_flat, units=1024, activation=tf.nn.relu)

  # Add dropout operation; 0.6 probability that element will be kept
  dropout = tf.layers.dropout(
      inputs=dense, rate=0.4, training=mode == tf.estimator.ModeKeys.TRAIN)

  # Logits layer
  # Input Tensor Shape: [batch_size, 1024]
  # Output Tensor Shape: [batch_size, 10]
  logits = tf.layers.dense(inputs=dropout, units=10)

  predictions = {
      # Generate predictions (for PREDICT and EVAL mode)
      "classes": tf.argmax(input=logits, axis=1),
      # Add `softmax_tensor` to the graph. It is used for PREDICT and by the
      # `logging_hook`.
      "probabilities": tf.nn.softmax(logits, name="softmax_tensor")
  }
  if mode == tf.estimator.ModeKeys.PREDICT:
    return tf.estimator.EstimatorSpec(mode=mode, predictions=predictions)

  # Calculate Loss (for both TRAIN and EVAL modes)
  loss = tf.losses.sparse_softmax_cross_entropy(labels=labels, logits=logits)

  # Configure the Training Op (for TRAIN mode)
  if mode == tf.estimator.ModeKeys.TRAIN:
    optimizer = tf.train.GradientDescentOptimizer(learning_rate=0.001)
    train_op = optimizer.minimize(
        loss=loss,
        global_step=tf.train.get_global_step())
    return tf.estimator.EstimatorSpec(mode=mode, loss=loss, train_op=train_op)

  # Add evaluation metrics (for EVAL mode)
#   eval_metric_ops = {
#       "accuracy": tf.metrics.accuracy(
#           labels=labels, predictions=predictions["classes"])}
#   return tf.estimator.EstimatorSpec(
#       mode=mode, loss=loss, eval_metric_ops=eval_metric_ops)


def main(unused_argv):
  # Load training and eval data
#   mnist = tf.contrib.learn.datasets.load_dataset("mnist")
#   train_data = mnist.train.images  # Returns np.array
#   train_labels = np.asarray(mnist.train.labels, dtype=np.int32)
#   print(train_data.shape)
#   print(len(train_labels))
#   eval_data = mnist.test.images  # Returns np.array
#   eval_labels = np.asarray(mnist.test.labels, dtype=np.int32)

  train_imgs_same, train_labels_same = load_data(img_dir_same, 1.0)
  train_imgs_diff, train_labels_diff = load_data(img_dir_diff, 0.0)  

  train_data_temp = np.concatenate([train_imgs_same, train_imgs_diff])
  train_labels_temp = np.append(train_labels_same, train_labels_diff)
        
  print(train_data_temp.shape)
  print(len(train_labels_temp))
  train_data, train_labels = shuffle(train_data_temp, train_labels_temp, random_state=0)  
  # Create the Estimator
  mnist_classifier = tf.estimator.Estimator(
      model_fn=cnn_model_fn, model_dir="/tmp/psvrt_base_convnet_model")

  # Set up logging for predictions
  # Log the values in the "Softmax" tensor with label "probabilities"
  tensors_to_log = {"probabilities": "softmax_tensor"}
  logging_hook = tf.train.LoggingTensorHook(
      tensors=tensors_to_log, every_n_iter=50)

  # Train the model
  train_input_fn = tf.estimator.inputs.numpy_input_fn(
      x={"x": train_data},
      y=train_labels,
      batch_size=100,
      num_epochs=None,
      shuffle=True)
  mnist_classifier.train(
      input_fn=train_input_fn,
      steps=20000,
      hooks=[logging_hook])

  # Evaluate the model and print results
#   eval_input_fn = tf.estimator.inputs.numpy_input_fn(
#       x={"x": eval_data},
#       y=eval_labels,
#       num_epochs=1,
#       shuffle=False)
#   eval_results = mnist_classifier.evaluate(input_fn=eval_input_fn)
#   print(eval_results)

# def main(unused_argv):
#   # Load training and eval data
#   mnist = tf.contrib.learn.datasets.load_dataset("mnist")
#   train_data = mnist.train.images  # Returns np.array
#   train_labels = np.asarray(mnist.train.labels, dtype=np.int32)
#   eval_data = mnist.test.images  # Returns np.array
#   eval_labels = np.asarray(mnist.test.labels, dtype=np.int32)

#   # Create the Estimator
#   mnist_classifier = tf.estimator.Estimator(
#       model_fn=cnn_model_fn, model_dir="/tmp/mnist_convnet_model")

#   # Set up logging for predictions
#   # Log the values in the "Softmax" tensor with label "probabilities"
#   tensors_to_log = {"probabilities": "softmax_tensor"}
#   logging_hook = tf.train.LoggingTensorHook(
#       tensors=tensors_to_log, every_n_iter=50)

#   # Train the model
#   train_input_fn = tf.estimator.inputs.numpy_input_fn(
#       x={"x": train_data},
#       y=train_labels,
#       batch_size=100,
#       num_epochs=None,
#       shuffle=True)
#   mnist_classifier.train(
#       input_fn=train_input_fn,
#       steps=20000,
#       hooks=[logging_hook])

#   # Evaluate the model and print results
#   eval_input_fn = tf.estimator.inputs.numpy_input_fn(
#       x={"x": eval_data},
#       y=eval_labels,
#       num_epochs=1,
#       shuffle=False)
#   eval_results = mnist_classifier.evaluate(input_fn=eval_input_fn)
#   print(eval_results)

In [5]:
tf.app.run()

(1000, 10800)
1000
INFO:tensorflow:Using default config.
INFO:tensorflow:Using config: {'_save_checkpoints_secs': 600, '_session_config': None, '_keep_checkpoint_max': 5, '_tf_random_seed': 1, '_keep_checkpoint_every_n_hours': 10000, '_save_checkpoints_steps': None, '_model_dir': '/tmp/psvrt_base_convnet_model', '_save_summary_steps': 100}
pool3.shape******
(100, 7, 7, 64)
INFO:tensorflow:Create CheckpointSaverHook.
INFO:tensorflow:Restoring parameters from /tmp/psvrt_base_convnet_model/model.ckpt-40001
INFO:tensorflow:Saving checkpoints for 40002 into /tmp/psvrt_base_convnet_model/model.ckpt.
INFO:tensorflow:loss = 0.00205337, step = 40002
INFO:tensorflow:probabilities = [[ 0.00001201  0.99998796  0.          0.          0.          0.          0.
   0.          0.          0.        ]
 [ 0.00849921  0.99150074  0.          0.          0.          0.          0.
   0.          0.          0.        ]
 [ 0.9999826   0.00001741  0.          0.          0.          0.          0.
   0.  

INFO:tensorflow:probabilities = [[ 1.          0.00000002  0.          0.          0.          0.          0.
   0.          0.          0.        ]
 [ 0.00011313  0.99988687  0.          0.          0.          0.          0.
   0.          0.          0.        ]
 [ 0.9998858   0.00011418  0.          0.          0.          0.          0.
   0.          0.          0.        ]
 [ 0.99998355  0.00001647  0.          0.          0.          0.          0.
   0.          0.          0.        ]
 [ 0.00000047  0.99999952  0.          0.          0.          0.          0.
   0.          0.          0.        ]
 [ 0.00000263  0.99999738  0.          0.          0.          0.          0.
   0.          0.          0.        ]
 [ 0.99999666  0.00000338  0.          0.          0.          0.          0.
   0.          0.          0.        ]
 [ 0.0002473   0.9997527   0.          0.          0.          0.          0.
   0.          0.          0.        ]
 [ 0.00214465  0.99785537  0.   

INFO:tensorflow:global_step/sec: 46.7521
INFO:tensorflow:loss = 0.00702186, step = 40102 (2.140 sec)
INFO:tensorflow:probabilities = [[ 0.00000105  0.99999893  0.          0.          0.          0.          0.
   0.          0.          0.        ]
 [ 0.0002551   0.99974483  0.          0.          0.          0.          0.
   0.          0.          0.        ]
 [ 0.00002063  0.99997938  0.          0.          0.          0.          0.
   0.          0.          0.        ]
 [ 0.          1.          0.          0.          0.          0.          0.
   0.          0.          0.        ]
 [ 0.00006628  0.99993372  0.          0.          0.          0.          0.
   0.          0.          0.        ]
 [ 0.00000599  0.99999404  0.          0.          0.          0.          0.
   0.          0.          0.        ]
 [ 0.99999881  0.00000119  0.          0.          0.          0.          0.
   0.          0.          0.        ]
 [ 0.99999976  0.00000029  0.          0.       

INFO:tensorflow:probabilities = [[ 0.99998426  0.00001574  0.          0.          0.          0.          0.
   0.          0.          0.        ]
 [ 0.00073194  0.99926811  0.          0.          0.          0.          0.
   0.          0.          0.        ]
 [ 0.00156848  0.9984315   0.          0.          0.          0.          0.
   0.          0.          0.        ]
 [ 0.00123773  0.99876225  0.          0.          0.          0.          0.
   0.          0.          0.        ]
 [ 0.99999654  0.0000035   0.          0.          0.          0.          0.
   0.          0.          0.        ]
 [ 0.96738684  0.03261321  0.          0.          0.          0.          0.
   0.          0.          0.        ]
 [ 0.99994063  0.00005936  0.          0.          0.          0.          0.
   0.          0.          0.        ]
 [ 0.99999654  0.00000341  0.          0.          0.          0.          0.
   0.          0.          0.        ]
 [ 0.00000048  0.99999952  0.   

INFO:tensorflow:global_step/sec: 44.923
INFO:tensorflow:loss = 0.00329605, step = 40202 (2.226 sec)
INFO:tensorflow:probabilities = [[ 0.00347341  0.99652654  0.          0.          0.          0.          0.
   0.          0.          0.        ]
 [ 0.          1.          0.          0.          0.          0.          0.
   0.          0.          0.        ]
 [ 0.99999523  0.0000048   0.          0.          0.          0.          0.
   0.          0.          0.        ]
 [ 0.99999893  0.00000107  0.          0.          0.          0.          0.
   0.          0.          0.        ]
 [ 0.99992764  0.00007232  0.          0.          0.          0.          0.
   0.          0.          0.        ]
 [ 0.00002521  0.99997485  0.          0.          0.          0.          0.
   0.          0.          0.        ]
 [ 0.00002937  0.99997067  0.          0.          0.          0.          0.
   0.          0.          0.        ]
 [ 0.00000012  0.99999988  0.          0.        

...

INFO:tensorflow:global_step/sec: 44.3179
INFO:tensorflow:loss = 0.000942615, step = 59902 (2.257 sec)
INFO:tensorflow:probabilities = [[ 1.          0.          0.          0.          0.          0.          0.
   0.          0.          0.        ]
 [ 0.00000199  0.99999797  0.          0.          0.          0.          0.
   0.          0.          0.        ]
 [ 0.99304056  0.00695945  0.          0.          0.          0.          0.
   0.          0.          0.        ]
 [ 0.00004309  0.99995697  0.          0.          0.          0.          0.
   0.          0.          0.        ]
 [ 0.00000024  0.99999976  0.          0.          0.          0.          0.
   0.          0.          0.        ]
 [ 0.99999142  0.00000859  0.          0.          0.          0.          0.
   0.          0.          0.        ]
 [ 0.00000746  0.99999249  0.          0.          0.          0.          0.
   0.          0.          0.        ]
 [ 0.00000036  0.99999964  0.          0.      

INFO:tensorflow:probabilities = [[ 1.          0.          0.          0.          0.          0.          0.
   0.          0.          0.        ]
 [ 0.99998796  0.00001198  0.          0.          0.          0.          0.
   0.          0.          0.        ]
 [ 0.99999809  0.00000197  0.          0.          0.          0.          0.
   0.          0.          0.        ]
 [ 0.0000168   0.99998319  0.          0.          0.          0.          0.
   0.          0.          0.        ]
 [ 0.00000002  1.          0.          0.          0.          0.          0.
   0.          0.          0.        ]
 [ 1.          0.00000001  0.          0.          0.          0.          0.
   0.          0.          0.        ]
 [ 1.          0.00000004  0.          0.          0.          0.          0.
   0.          0.          0.        ]
 [ 0.99999356  0.00000642  0.          0.          0.          0.          0.
   0.          0.          0.        ]
 [ 0.99999988  0.00000015  0.   

INFO:tensorflow:Saving checkpoints for 60001 into /tmp/psvrt_base_convnet_model/model.ckpt.
INFO:tensorflow:Loss for final step: 0.000725404.


SystemExit: 

/home/asaeed9/anaconda2/lib/python2.7/site-packages/IPython/core/interactiveshell.py:2889: UserWarning: To exit: use 'exit', 'quit', or Ctrl-D.
  warn("To exit: use 'exit', 'quit', or Ctrl-D.", stacklevel=1)


In [ ]:
train_imgs_same, train_labels_same = load_data(img_dir_same, 1)
train_imgs_diff, train_labels_diff = load_data(img_dir_diff, 0)

# train_imgs = np.append(train_imgs_same, train_imgs_diff)
train_imgs = np.concatenate([train_imgs_same, train_imgs_diff])
train_lbls = np.append(train_labels_same, train_labels_diff)
print(len(train_lbls))
print(len(train_imgs), train_imgs.shape, len(train_lbls))
print(len(train_imgs_same), train_imgs_same.shape, len(train_labels_same))
print(len(train_imgs_diff), train_imgs_diff.shape, len(train_labels_diff))

print(train_imgs, train_lbls)
X, y = shuffle(train_imgs, train_lbls, random_state=0)
print(X, y)

In [6]:
tf.__version__




'1.2.0'

In [ ]:
?